In [2]:
import numpy as np
import pandas as pd
import os
from tqdm import tqdm_notebook as tqdm

In [2]:
data = pd.read_pickle("../Data/Guitar/pipeline_test.pkl")

In [3]:
data["N_notes"] = 0
for index, row in data.iterrows():
    data.iloc[index, 3] = len(row["Sheet"])

In [4]:
data = data.sort_values("Riff").reset_index(drop=True)

In [5]:
data.to_pickle("../Data/Guitar/pipeline_test.pkl")

In [6]:
data.head()

Riff                                              Sheet  Tempo  N_notes
0  18-0  [[5.0, 4.0, 1.0], [5.0, 4.0, 0.5], [5.0, 4.0, ...  140.0       12
1  18-1  [[6.0, 4.0, 1.0], [6.0, 4.0, 0.5], [6.0, 4.0, ...  140.0       12
2  18-2  [[7.0, 4.0, 1.0], [7.0, 4.0, 0.5], [7.0, 4.0, ...  140.0       12
3  18-3  [[8.0, 4.0, 1.0], [8.0, 4.0, 0.5], [8.0, 4.0, ...  140.0       12
4  18-4  [[9.0, 4.0, 1.0], [9.0, 4.0, 0.5], [9.0, 4.0, ...  140.0       12

In [4]:
%run Sheet_generator.ipynb

Instructions for updating:
Colocations handled automatically by placer.
Instructions for updating:
Please use `rate` instead of `keep_prob`. Rate should be set to `rate = 1 - keep_prob`.


In [1]:
%run ../Utilities/Utilities.ipynb

Using TensorFlow backend.


In [ ]:
results = pd.DataFrame()
pbar = tqdm(os.listdir("../Samples/Guitar/Test_riffs/"))
    
for file in pbar:
    pbar.set_description("Processing %s" % file)
    
    SG = sheet_generator("../Single_note_models/Guitar/Guitar", "../Single_note_models/Guitar/Guitar_norm_string", 
                         "../Tempo/tempo_lgbm.txt")
    pred = SG.note_extraction(waveform("../Samples/Guitar/Test_riffs/" + file), False)
    sheet = SG.raw_sheet(pred, True)
    
    results = results.append({"Riff": file[17:].split(".")[0].replace("_", "-"), 
                              "Tempo": SG.bpm, "Sheet": sheet[:,1:4].tolist()}, ignore_index=True)

E:\Anaconda\envs\tfm\lib\site-packages\numpy\core\fromnumeric.py:3118: RuntimeWarning: Mean of empty slice.
  out=out, **kwargs)
E:\Anaconda\envs\tfm\lib\site-packages\numpy\core\_methods.py:85: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)


In [10]:
results["N_notes"] = 0
for index, row in results.iterrows():
    results.iloc[index, 3] = len(row["Sheet"])

In [4]:
results.head()

Riff                                              Sheet  Tempo  N_notes
0    18  [[4, 0.39473684210526316, 5], [4, 0.1973684210...  152.0       12
1  18-1  [[4, 0.46511627906976744, 6], [4, 0.2325581395...  129.0       10
2  18-2  [[4, 0.40540540540540543, 7], [4, 0.2027027027...  148.0       13
3  18-3  [[4, 0.39215686274509803, 8], [4, 0.1960784313...  153.0       12
4  18-4  [[4, 0.40268456375838924, 9], [4, 0.3020134228...  149.0       12

In [12]:
results.to_pickle("../Data/Guitar/pipeline_test_preds.pkl")

In [43]:
data[data["Riff"] == "18-1"]["Sheet"].values[0]

[[6.0, 4.0, 1.0],
 [6.0, 4.0, 0.5],
 [6.0, 4.0, 1.0],
 [4.0, 4.0, 0.5],
 [5.0, 3.0, 0.5],
 [3.0, 3.0, 0.5],
 [5.0, 3.0, 1.0],
 [4.0, 2.0, 0.25],
 [6.0, 2.0, 0.25],
 [4.0, 2.0, 1.0],
 [6.0, 3.0, 0.5],
 [5.0, 3.0, 1.0]]

In [44]:
results[results["Riff"] == "18-1"]["Sheet"].values[0]

[[4, 0.46511627906976744, 6],
 [4, 0.23255813953488372, 6],
 [4, 0.6976744186046512, 6],
 [3, 0.23255813953488372, 5],
 [3, 0.23255813953488372, 3],
 [3, 0.3488372093023256, 5],
 [2, 0.23255813953488372, 4],
 [2, 0.46511627906976744, 4],
 [3, 0.23255813953488372, 6],
 [3, 0.46511627906976744, 5]]

## Performance

In [3]:
results = pd.read_pickle("../Data/Guitar/pipeline_test_preds.pkl")
data = pd.read_pickle("../Data/Guitar/pipeline_test.pkl")

### Overall

In [14]:
correct_notes = 0
total_notes = 0
for index, row_pred in results.iterrows():
    row_true = data.iloc[index]
    bpm = row_true["Tempo"]
    sheet_true = row_true["Sheet"].copy()
    sheet_pred = row_pred["Sheet"].copy()
    i = 0
    
    while i < len(sheet_true):
        beats_pred = round_to_base(sheet_pred[i][1] * (1/60) * bpm, 0.25)
        
        if (sheet_true[i][0] == sheet_pred[i][2]) and (sheet_true[i][1] == sheet_pred[i][0]) and (sheet_true[i][2] == beats_pred):
            correct_notes += 1
            i += 1
            
        else:
            if len(sheet_pred) > len(sheet_true):
                # Skip this predicted note
                del sheet_pred[i]
                
            elif len(sheet_pred) < len(sheet_true):
                # Skip this true note
                del sheet_true[i]
            else:
                i += 1
                
        total_notes += 1
        
print(correct_notes/total_notes)

0.6312154696132597


# Performance - Manual

In [8]:
performance = pd.read_csv("Performance/Test/performance.tsv", sep="\t", header=0)

In [10]:
performance.head()

Riff  Total  Hits_overall  Hits_seg  Hits_note  Hits_string
0    18     12            10        12         12           10
1  18-1     12            10        10         10           10
2  18-2     13            12        12         12           12
3  18-3     12            11        12         12           11
4  18-4     12            12        12         12           11

### Overall

In [18]:
performance["Hits_overall"].sum()/performance["Total"].sum()

0.839142091152815

### Segmentation

In [19]:
performance["Hits_seg"].sum()/performance["Total"].sum()

0.9463806970509383

### Note ID

In [20]:
performance["Hits_note"].sum()/performance["Hits_seg"].sum()

0.9631728045325779

### String ID

In [21]:
performance["Hits_string"].sum()/performance["Hits_seg"].sum()

0.9036827195467422